In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import *

In [0]:
# Load AWS Credentials
spark.conf.set("fs.s3a.access.key", "<aws_access_key_id>")
spark.conf.set("fs.s3a.secret.key", "<aws_secret_access_key>")

In [0]:
# Read Yellow and Green Taxi DataFrames and drop duplicate rows
yellow_taxi_df = spark.read.option("recursiveFileLookup", "true").parquet("s3://capstone-techcatalyst-raw/yellow_taxi/*",multiLine=True, encoding="utf8").drop_duplicates()
green_taxi_df = spark.read.option("recursiveFileLookup", "true").parquet("s3://capstone-techcatalyst-raw/green_taxi/*",multiLine=True, encoding="utf8").drop_duplicates()

In [0]:
# Fill null values based on assumptions 
yellow_taxi_df = yellow_taxi_df.fillna({'passenger_count':1, 'congestion_surcharge':0, 'Airport_fee':0})
green_taxi_df = green_taxi_df.fillna({'passenger_count':1, 'congestion_surcharge':0})

In [0]:
# Rename pickup and dropoff column names to match for both DataFrames
yellow_taxi_df = yellow_taxi_df.withColumnRenamed("tpep_pickup_datetime", "pickup_datetime").withColumnRenamed("tpep_dropoff_datetime", "dropoff_datetime")
green_taxi_df = green_taxi_df.withColumnRenamed("lpep_pickup_datetime", "pickup_datetime").withColumnRenamed("lpep_dropoff_datetime", "dropoff_datetime")

# Add columns that are in one DataFrame but not the other
# Add a Taxi_Type column (Yellow or Green)
green_taxi_df = green_taxi_df.withColumn("Airport_fee", lit(None)).withColumn("Taxi_Type", lit("Green"))
yellow_taxi_df = yellow_taxi_df.withColumn("ehail_fee", lit(None)).withColumn("trip_type", lit(None)).withColumn("Taxi_Type", lit("Yellow"))

# Combine the yellow and green taxi DataFrames into one DataFrame based on column names
taxi_df = yellow_taxi_df.unionByName(green_taxi_df)

In [0]:
# Create datetime column called "date" based on the pickup date
taxi_df = taxi_df.withColumn("date", taxi_df["pickup_datetime"].cast("date"))

In [0]:
# Add additional date feature columns based on the date column
taxi_df = taxi_df.withColumn("year", date_format('date', 'yyyy'))
taxi_df = taxi_df.withColumn("month", date_format('date', 'MM'))
taxi_df = taxi_df.withColumn("day_of_month", dayofmonth('date'))
taxi_df = taxi_df.withColumn("day_of_week", date_format('date', 'EEEE')) 
taxi_df = taxi_df.withColumn("is_weekend", dayofweek("date").isin([1,7]).cast("boolean"))
taxi_df = taxi_df.withColumn('trip_duration', (unix_timestamp('dropoff_datetime') - unix_timestamp('pickup_datetime'))/60)

# Filter DataFrame to only include rows where the date is between September 2023 - May 2024
taxi_df = taxi_df.filter(taxi_df["date"].between("2023-09-01", "2024-05-31"))  

In [0]:
display(taxi_df)

VendorID pickup_datetime dropoff_datetime passenger_count trip_distance RatecodeID store_and_fwd_flag PULocationID DOLocationID payment_type fare_amount extra mta_tax tip_amount tolls_amount improvement_surcharge total_amount congestion_surcharge Airport_fee ehail_fee trip_type Taxi_Type date year month day_of_month day_of_week is_weekend trip_duration 2 2024-05-01T00:09:30.000+0000 2024-05-01T00:34:42.000+0000 1 9.78 1 N 76 89 2 40.8 1.0 0.5 0.0 0.0 1.0 43.3 0.0 0.0 null null Yellow 2024-05-01 2024 05 1 Wednesday false 25.2 2 2024-05-01T00:49:08.000+0000 2024-05-01T00:59:35.000+0000 1 2.2 1 N 48 141 1 12.8 1.0 0.5 3.56 0.0 1.0 21.36 2.5 0.0 null null Yellow 2024-05-01 2024 05 1 Wednesday false 10.45 2 2024-05-01T00:37:00.000+0000 2024-05-01T00:41:36.000+0000 2 0.86 1 N 68 50 1 7.2 1.0 0.5 2.44 0.0 1.0 14.64 2.5 0.0 null null Yellow 2024-05-01 2024 05 1 Wednesday false 4.6 2 2024-05-01T00:29:39.000+0000 2024-05-01T00:48:23.000+0000 1 3.3 1 N 230 262 1 20.5 1.0 0.5 6.38 0.0 1.0 31.88 2.5 0.0 null null Yellow 2024-05-01 2024 05 1 Wednesday false 18.733333333333334 2 2024-05-01T00:13:08.000+0000 2024-05-01T00:28:02.000+0000 3 2.85 1 N 237 249 1 16.3 1.0 0.5 5.32 0.0 1.0 26.62 2.5 0.0 null null Yellow 2024-05-01 2024 05 1 Wednesday false 14.9 2 2024-05-01T01:34:21.000+0000 2024-05-01T01:38:01.000+0000 1 1.29 1 N 263 75 4 -7.2 -1.0 -0.5 0.0 0.0 -1.0 -12.2 -2.5 0.0 null null Yellow 2024-05-01 2024 05 1 Wednesday false 3.6666666666666665 2 2024-05-01T01:46:19.000+0000 2024-05-01T01:50:58.000+0000 1 1.06 1 N 162 140 1 7.2 1.0 0.5 2.0 0.0 1.0 14.2 2.5 0.0 null null Yellow 2024-05-01 2024 05 1 Wednesday false 4.65 2 2024-05-01T01:29:29.000+0000 2024-05-01T01:35:35.000+0000 2 1.04 1 N 249 90 1 7.9 1.0 0.5 2.58 0.0 1.0 15.48 2.5 0.0 null null Yellow 2024-05-01 2024 05 1 Wednesday false 6.1 2 2024-05-01T01:48:26.000+0000 2024-05-01T01:54:06.000+0000 1 1.28 1 N 186 246 1 8.6 1.0 0.5 2.72 0.0 1.0 16.32 2.5 0.0 null null Yellow 2024-05-01 2024 05 1 Wednesday false 5.666666666666667 2 2024-05-01T01:16:46.000+0000 2024-05-01T01:21:46.000+0000 1 0.88 1 N 107 170 1 7.2 1.0 0.5 3.66 0.0 1.0 15.86 2.5 0.0 null null Yellow 2024-05-01 2024 05 1 Wednesday false 5.0 2 2024-05-01T01:03:00.000+0000 2024-05-01T01:12:01.000+0000 1 1.36 1 N 79 148 1 10.7 1.0 0.5 2.0 0.0 1.0 17.7 2.5 0.0 null null Yellow 2024-05-01 2024 05 1 Wednesday false 9.016666666666667 2 2024-05-01T01:30:33.000+0000 2024-05-01T01:36:17.000+0000 1 1.1 1 N 237 170 2 7.9 1.0 0.5 0.0 0.0 1.0 12.9 2.5 0.0 null null Yellow 2024-05-01 2024 05 1 Wednesday false 5.733333333333333 2 2024-05-01T01:04:02.000+0000 2024-05-01T01:47:26.000+0000 5 18.85 2 N 132 163 1 70.0 0.0 0.5 16.54 6.94 1.0 99.23 2.5 1.75 null null Yellow 2024-05-01 2024 05 1 Wednesday false 43.4 2 2024-05-01T01:39:54.000+0000 2024-05-01T02:23:57.000+0000 2 20.35 2 N 10 87 1 70.0 0.0 0.5 14.8 0.0 1.0 88.8 2.5 0.0 null null Yellow 2024-05-01 2024 05 1 Wednesday false 44.05 2 2024-05-01T03:09:45.000+0000 2024-05-01T03:17:36.000+0000 1 2.32 1 N 211 33 1 12.1 1.0 0.5 3.42 0.0 1.0 20.52 2.5 0.0 null null Yellow 2024-05-01 2024 05 1 Wednesday false 7.85 2 2024-05-01T03:38:42.000+0000 2024-05-01T03:48:29.000+0000 1 3.72 1 N 79 80 4 -18.4 -1.0 -0.5 0.0 0.0 -1.0 -23.4 -2.5 0.0 null null Yellow 2024-05-01 2024 05 1 Wednesday false 9.783333333333333 2 2024-05-01T04:57:42.000+0000 2024-05-01T05:17:53.000+0000 1 10.36 1 N 239 138 1 41.5 6.0 0.5 3.0 6.94 1.0 61.44 2.5 0.0 null null Yellow 2024-05-01 2024 05 1 Wednesday false 20.183333333333334 2 2024-05-01T05:54:17.000+0000 2024-05-01T06:00:51.000+0000 1 1.76 1 N 236 161 1 10.0 1.0 0.5 2.25 0.0 1.0 17.25 2.5 0.0 null null Yellow 2024-05-01 2024 05 1 Wednesday false 6.566666666666666 2 2024-05-01T05:34:40.000+0000 2024-05-01T06:00:41.000+0000 1 16.75 2 N 162 132 1 70.0 0.0 0.5 16.19 6.94 1.0 97.13 2.5 0.0 null null Yellow 2024-05-01 2024 05 1 Wednesday false 26.016666666666666 1 2024-05-01T05:17:23.000+0000 2024-05-01T05:22:52.000+0000 1 0.7 99 N 74 74 1 15.5 0.0 0.5 0.0 0.0 1.0 17.0 0.0 0.0 nul

In [0]:
# Count null values in each column
display(taxi_df.select([sum(col(c).isNull().cast("integer")).alias(c) for c in taxi_df.columns]))

VendorID pickup_datetime dropoff_datetime passenger_count trip_distance RatecodeID store_and_fwd_flag PULocationID DOLocationID payment_type fare_amount extra mta_tax tip_amount tolls_amount improvement_surcharge total_amount congestion_surcharge Airport_fee ehail_fee trip_type Taxi_Type date year month day_of_month day_of_week is_weekend trip_duration 0 0 0 0 0 2204270 2204270 0 0 31234 0 0 0 0 0 0 0 0 544905 30423026 29909403 0 0 0 0 0 0 0 0

In [0]:
# Write taxi DataFrame to parquet files partitioned by year, month, and taxi type
taxi_df = taxi_df.withColumn("year_", col("year"))
taxi_df = taxi_df.withColumn("month_", col("month"))
taxi_df = taxi_df.withColumn("taxi_type_", col("Taxi_Type"))

taxi_parquet_path = f"s3a://capstone-techcatalyst-conformed/group4/taxi_data/"

taxi_df.write.partitionBy(["year_", "month_", "taxi_type_"]).parquet(taxi_parquet_path)